In [45]:
import pandas as pd

# Path to your dataset folder
path = r"C:/Users/Acer/Desktop/ppp/"

# Load the files
listings = pd.read_csv(path + "listings.csv.gz", compression='gzip')
calendar = pd.read_csv(path + "calendar.csv.gz", compression='gzip')
reviews = pd.read_csv(path + "reviews.csv.gz", compression='gzip')

# Check first rows
listings.head()


id                         listing_url       scrape_id last_scraped  \
0  18674  https://www.airbnb.com/rooms/18674  20250914152803   2025-09-15   
1  23197  https://www.airbnb.com/rooms/23197  20250914152803   2025-09-14   
2  32711  https://www.airbnb.com/rooms/32711  20250914152803   2025-09-15   
3  34241  https://www.airbnb.com/rooms/34241  20250914152803   2025-09-15   
4  34981  https://www.airbnb.com/rooms/34981  20250914152803   2025-09-15   

        source                                               name  \
0  city scrape    Huge flat for 8 people close to Sagrada Familia   
1  city scrape  Forum CCIB DeLuxe, Spacious, Large Balcony, relax   
2  city scrape                   Sagrada Familia area - Còrsega 1   
3  city scrape   Stylish Top Floor Apartment - Ramblas Plaza Real   
4  city scrape               VIDRE HOME PLAZA REAL on LAS RAMBLAS   

                                         description  \
0  110m2 apartment to rent in Barcelona. Located ...   
1  Beautiful and Spacious Apartment with Large Te...   
2  A lovely two bedroom apartment only 250 m from...   
3  Located in close proximity to Plaza Real and L...   
4  Spacious apartment for large families or group...   

                               neighborhood_overview  \
0  Apartment in Barcelona located in the heart of...   
1  Strategically located in the Parc del Fòrum, a...   
2  What's nearby  <br />This apartment is located...   
3                                                NaN   
4  Located in Ciutat Vella in the Gothic Quarter,...   

                                         picture_url  host_id  ...  \
0  https://a0.muscache.com/pictures/13031453/413c...    71615  ...   
1  https://a0.muscache.com/pictures/miso/Hosting-...    90417  ...   
2  https://a0.muscache.com/pictures/357b25e4-f414...   135703  ...   
3  https://a0.muscache.com/pictures/2437facc-2fe7...    73163  ...   
4  https://a0.muscache.com/pictures/c4d1723c-e479...    73163  ...   

  review_scores_communication review_scores_location review_scores_value  \
0                        4.62                   4.82                4.32   
1                        4.99                   4.66                4.68   
2                        4.89                   4.89                4.47   
3                        4.68                   4.73                4.23   
4                        4.72                   4.65                4.46   

                                             license instant_bookable  \
0  ESFCTU000008058000039706000000000000000HUTB-00...                t   
1  ESFCTU000008106000547162000000000000000000HUTB...                f   
2                                        HUTB-001722                f   
3                                             Exempt                f   
4  ESFCTU000008119000093652000000000000000HUTB-00...                f   

  calculated_host_listings_count calculated_host_listings_count_entire_homes  \
0                             26                                          26   
1                              1                                           1   
2                              2                                           2   
3                              3                                           3   
4                              3                                           3   

  calculated_host_listings_count_private_rooms  \
0                                            0   
1                                            0   
2                                            0   
3                                            0   
4                                            0   

  calculated_host_listings_count_shared_rooms reviews_per_month  
0                                           0              0.34  
1                                           0              0.52  
2                                           0              0.88  
3                                           0              0.14  
4                        

In [46]:
df_listings = listings
df_calendar = calendar
df_reviews = reviews


In [47]:
# Calendar is too big → sample 100k rows
df_calendar_small = df_calendar.sample(100000, random_state=42)


In [48]:
df = df_calendar_small.merge(
    df_listings,
    how="left",
    left_on="listing_id",
    right_on="id"
)

df = df.drop(columns=["id"])


In [49]:
df_reviews_agg = df_reviews.groupby("listing_id").agg(
    n_reviews=("id", "count"),
    first_review=("date", "min"),
    last_review=("date", "max")
).reset_index()


In [50]:
df = df.merge(
    df_reviews_agg,
    how="left",
    on="listing_id"
)


In [51]:
print(df.shape)
df.head()
df.info()


(100000, 88)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 88 columns):
 #   Column                                        Non-Null Count   Dtype  
---  ------                                        --------------   -----  
 0   listing_id                                    100000 non-null  int64  
 1   date                                          100000 non-null  object 
 2   available                                     100000 non-null  object 
 3   price_x                                       0 non-null       float64
 4   adjusted_price                                0 non-null       float64
 5   minimum_nights_x                              100000 non-null  int64  
 6   maximum_nights_x                              100000 non-null  int64  
 7   listing_url                                   100000 non-null  object 
 8   scrape_id                                     100000 non-null  int64  
 9   last_scraped                        

In [52]:
# Missing values per column
df.isna().sum().sort_values(ascending=False).head(20)


price_x                        100000
adjusted_price                 100000
calendar_updated               100000
host_neighbourhood              55171
neighbourhood                   53505
neighborhood_overview           53505
host_about                      36700
license                         28290
review_scores_checkin           25672
review_scores_accuracy          25669
review_scores_location          25664
review_scores_value             25664
review_scores_cleanliness       25664
review_scores_communication     25656
reviews_per_month               25651
review_scores_rating            25651
last_review_x                   25651
first_review_x                  25651
n_reviews                       25651
first_review_y                  25651
dtype: int64

In [53]:
df.describe()


listing_id  price_x  adjusted_price  minimum_nights_x  \
count  1.000000e+05      0.0             0.0      100000.00000   
mean   6.201547e+17      NaN             NaN          19.08421   
std    5.893809e+17      NaN             NaN          48.66281   
min    1.867400e+04      NaN             NaN           1.00000   
25%    3.054739e+07      NaN             NaN           2.00000   
50%    7.014493e+17      NaN             NaN           4.00000   
75%    1.180999e+18      NaN             NaN          31.00000   
max    1.509435e+18      NaN             NaN        1124.00000   

       maximum_nights_x     scrape_id       host_id  host_listings_count  \
count      1.000000e+05  1.000000e+05  1.000000e+05         99981.000000   
mean       3.012232e+05  2.025091e+13  2.111255e+08            83.720287   
std        2.540771e+07  3.061343e+01  2.146626e+08           179.255258   
min        1.000000e+00  2.025091e+13  3.073000e+03             1.000000   
25%        3.300000e+02  2.025091e+13  1.313159e+07             2.000000   
50%        3.650000e+02  2.025091e+13  1.384062e+08             9.000000   
75%        1.125000e+03  2.025091e+13  3.676136e+08            47.000000   
max        2.147484e+09  2.025091e+13  7.186126e+08           994.000000   

       host_total_listings_count       latitude  ...  review_scores_checkin  \
count               99981.000000  100000.000000  ...           74328.000000   
mean                  110.842770      41.392292  ...               4.711825   
std                   225.586252       0.014023  ...               0.496748   
min                     1.000000      41.351783  ...               0.000000   
25%                     3.000000      41.381194  ...               4.670000   
50%                    13.000000      41.390140  ...               4.860000   
75%                    81.000000      41.401600  ...               5.000000   
max                  2706.000000      41.462243  ...               5.000000   

       review_scores_communication  review_scores_location  \
count                 74344.000000            74336.000000   
mean                      4.708533                4.746810   
std                       0.516949                0.396954   
min                       0.000000                0.000000   
25%                       4.670000                4.680000   
50%                       4.860000                4.850000   
75%                       5.000000                5.000000   
max                       5.000000                5.000000   

       review_scores_value  calculated_host_listings_count  \
count         74336.000000                   100000.000000   
mean              4.452457                       61.788630   
std               0.582540                      123.115833   
min               0.000000                        1.000000   
25%               4.320000                        2.000000   
50%               4.570000                        7.000000   
75%               4.790000                       39.000000   
max               5.000000                      514.000000   

       calculated_host_listings_count_entire_homes  \
count                                100000.000000   
mean                                     45.131230   
std                                     109.334068   
min                                       0.000000   
25%                                       0.000000   
50%                                       3.000000   
75%                                      23.000000   
max                                     514.000000   

       calculated_host_listings_count_private_rooms  \
count                                 100000.000000   
mean                                      16.521690   
std                                       65.811103   
min                                        0.000000   
25%                                        0.000000   
50%                                        0.000000   
75%                        

In [54]:
df.describe(include="object").T


count unique  \
date                          100000    366   
available                     100000      2   
listing_url                   100000  19303   
last_scraped                  100000      2   
source                        100000      2   
name                          100000  18426   
description                    96119  15462   
neighborhood_overview          46495   6066   
picture_url                   100000  19035   
host_url                      100000   6590   
host_name                      99981   3212   
host_since                     99981   3514   
host_location                  76021    405   
host_about                     63300   3215   
host_response_time             83985      4   
host_response_rate             83985     70   
host_acceptance_rate           85957    100   
host_is_superhost              98016      2   
host_thumbnail_url             99981   6305   
host_picture_url               99981   6305   
host_neighbourhood             44829    139   
host_verifications             99981      8   
host_has_profile_pic           99981      2   
host_identity_verified         99981      2   
neighbourhood                  46495     49   
neighbourhood_cleansed        100000     71   
neighbourhood_group_cleansed  100000     10   
property_type                 100000     51   
room_type                     100000      4   
bathrooms_text                 99936     38   
amenities                     100000  16235   
price_y                        78834    772   
has_availability               94539      1   
calendar_last_scraped         100000      2   
first_review_x                 74349   3797   
last_review_x                  74349   1836   
license                        71710   7494   
instant_bookable              100000      2   
first_review_y                 74349   3797   
last_review_y                  74349   1836   

                                                                            top  \
date                                                                 2025-09-20   
available                                                                     t   
listing_url                    https://www.airbnb.com/rooms/1060268743089157821   
last_scraped                                                         2025-09-15   
source                                                              city scrape   
name                                                    Habitación en Barcelona   
description                   Our mission is to empower individuals to immer...   
neighborhood_overview         A modernist treasure trove full of elaborate a...   
picture_url                   https://a0.muscache.com/pictures/miso/Hosting-...   
host_url                            https://www.airbnb.com/users/show/346367515   
host_name                                                                  Ukio   
host_since                                                           2020-05-15   
host_location                                                  Barcelona, Spain   
host_about                    At Ukio, we've redefined the concept of living...   
host_response_time                                               within an hour   
host_response_rate                                                         100%   
host_acceptance_rate                                                       100%   
host_is_superhost                                                             f   
host_thumbnail_url            https://a0.muscache.com/defaults/user_pic-50x5...   
host_picture_url              https://a0.muscache.com/defaults/user_pic-225x...   
host_neighbourhood                                          Dreta de l'Eixample   
host_verifications                                           ['email', 'phone']   
host_has_profile_pic                                                          t   
host_identity_verified                                                        t   
neighbourhood               

In [55]:
df["date"] = pd.to_datetime(df["date"], errors="coerce")


In [56]:
import plotly.express as px

df_date = df["date"].value_counts().sort_index()

fig = px.line(
    df_date,
    title="Listings per Date",
    labels={"value": "Listings", "index": "Date"}
)

fig.show()


**Insight:** The number of listings across dates stays relatively stable, showing a consistent supply of Airbnb listings during the selected period.


In [59]:
top_neigh = df["neighborhood_overview"].value_counts().head(10)

fig = px.bar(
    top_neigh,
    title="Top 10 Neighbourhoods",
    labels={"value": "Count", "index": "Neighbourhood"}
)
fig.show()


📌 1. Top 10 Neighbourhoods

Insights:

These are the neighbourhoods with the highest number of listings.

More listings usually means:

High tourist demand

Good location / accessibility

Popular attractions nearby

These top 10 neighbourhoods dominate the Airbnb market of the city.

In [67]:
fig = px.density_heatmap(df, x="date", y="available",
                         title="Availability Heatmap")
fig.show()


2. Availability Heatmap

Insights:

There is a strong seasonal pattern in availability.

Certain months show higher availability, meaning:

Lower demand

Possibly off-season for tourism

Other periods show very low availability, suggesting:

High tourist influx

Peak season / holidays / events

The heatmap gives a quick overview of how Airbnb supply fluctuates over the year.

In [60]:
fig = px.histogram(
    df, 
    x="n_reviews", 
    nbins=50,
    title="Distribution of Number of Reviews"
)
fig.show()


📌 3. Distribution of Number of Reviews

Insights:

Most listings have very few reviews, indicating:

Many new or rarely booked listings

A small number of listings have very high reviews, which means:

They are very popular

Strong guest satisfaction

High occupancy rate

The distribution is heavily right-skewed, typical for marketplaces.

In [69]:
df_daily_availability = df.groupby("date")["available"].value_counts().rename("count").reset_index()

fig = px.line(df_daily_availability, x="date", y="count", color="available",
              title="Availability Over Time")
fig.show()


📌 4. Availability Over Time

Insights:

The number of available (t) and not available (f) listings changes over time.

The lines suggest:

Seasonal dips when listings get booked heavily

Gradual variations throughout the year

Comparing the two helps understand:

When booking activity is highest

Possible tourism cycles

This is useful for predicting demand periods.

In [70]:
df_neighborhood = df["neighborhood_overview"].value_counts().reset_index()
df_neighborhood.columns = ["neighborhood", "count"]

fig = px.bar(df_neighborhood.head(20),  # top 20 only
             x="neighborhood", y="count",
             title="Top 20 Neighborhoods with Most Listings")
fig.show()


### 📍 Insights: Top 20 Neighborhoods with Most Listings
- Some neighborhoods have **way more Airbnb listings** than others.
- The first 3–5 neighborhoods completely dominate the supply.
- This means these areas are the **most popular or crowded** for hosts.
- If Airbnb predicts demand, these neighborhoods are “hot zones.”


In [61]:
fig = px.histogram(
    df, 
    x="minimum_nights_x",
    nbins=50,
    title="Distribution of Minimum Nights"
)
fig.show()


### 🛌 Insights: Minimum Nights Required
- Most listings have **very low minimum nights** (like 1–3 nights).
- Only a few listings require huge minimum stays (100+ nights).
- This tells us the market is mainly for **short-term stays**, not long monthly rentals.
- Long minimum-night values are rare and look like outliers.


In [66]:
df_daily_reviews = df.groupby("date")["n_reviews"].sum().reset_index()

fig = px.line(df_daily_reviews, x="date", y="n_reviews",
              title="Total Reviews per Day")
fig.show()


### ⭐ Insights: Total Reviews per Day
- Review counts bounce up and down daily but stay in a similar range.
- This means customer activity is **consistent** across the year.
- Occasional spikes show days where **lots of guests reviewed** at once.
- No huge drop or rise → platform demand is stable.


In [71]:
df_host = df["host_id"].value_counts().reset_index()
df_host.columns = ["host_id", "num_listings"]

fig = px.histogram(df_host, x="num_listings", nbins=50,
                   title="Distribution of Number of Listings per Host")
fig.show()


### 👤 Insights: Number of Listings per Host
- Most hosts only have **1 or 2 listings**.
- A very small number of hosts own **hundreds or thousands** of listings.
- This means the platform is mostly **small individual hosts**, with a few **big business hosts** dominating the rest.
- Classic “long tail” distribution.


In [72]:
df_daily_reviews = df.groupby("date")["n_reviews"].sum().reset_index()

fig = px.line(df_daily_reviews, x="date", y="n_reviews",
              title="Total Reviews per Day")
fig.show()


### ⭐ Insights: Total Reviews Per Day
- The number of reviews each day stays in a **steady range**.
- There are small ups and downs, but no big spikes or crashes.
- This means guests are using Airbnb **consistently throughout the year**.
- The steady pattern shows **stable customer demand** over time.


# 📊 Exploratory Data Analysis — Summary of Insights

### **1. Listings Activity Over Time**
The number of active Airbnb listings remains stable across the observed dates, indicating a consistent supply of listings in the selected city with no major spikes or drops.

### **2. Availability Behavior**
Availability fluctuates on a day-to-day basis. Certain days show more available listings while others show more booked listings, suggesting seasonal effects or weekly booking patterns.

### **3. Review Dynamics**
Total reviews per day show continuous but uneven guest engagement. Peaks in review activity may correspond to holidays, high-tourism periods, or events happening in the city.

### **4. Host Listing Distribution**
Most hosts own only a single listing, indicating that the platform is dominated by individual property owners. A small group of hosts owns multiple listings, representing professional hosts or rental companies.

### **5. Neighborhood Distribution**
Listings are unevenly distributed across neighborhoods. Some neighborhoods have a significantly higher concentration of listings, likely reflecting tourist-friendly or high-demand locations.

---

### **Overall Conclusion**
The dataset shows strong temporal patterns (availability + reviews), clear neighborhood clustering, and strong host asymmetry. These patterns guide the feature engineering phase and support the predictive modeling task that follows.Overall, the analysis gives a clear picture of how Airbnb activity behaves across time, neighborhoods, host behavior, and guest demand:

Listings are heavily concentrated in a small group of neighborhoods, meaning a few areas dominate the market and attract most of the hosts and guests.

Availability patterns show clear seasonal cycles, with drops and spikes throughout the year — suggesting periods of high demand (holidays, events, summer) and quieter months.

Review activity stays consistently high, proving that the platform is actively used across the entire year, and guest turnover remains strong.

Most hosts manage very few listings, but a small number of hosts control a large chunk of the market, showing typical Airbnb “power hosts.”

Minimum nights are usually low, meaning short stays are the main business model, but there are rare outliers with huge minimum-night requirements.

👉 In simple words:

The market is active, seasonal, and dominated by a few neighborhoods and power hosts, with constant guest activity throughout the year. This gives a stable base for forecasting demand, optimizing pricing, and creating features for any ML model.
